In [ ]:
import numpy as np
import numpy.ma as ma

import pandas as pd
import os
from scipy.stats.mstats import theilslopes

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

import warnings
warnings.filterwarnings('ignore')

In [ ]:
#Test on synthetic case
def nlm(tlen, dt, dt_index, x0, p0, sigma, sin_model):
    def prop(x, p0):
        return -p0 + x - x**3
    x = np.zeros(tlen)
    x[0] = x0
    noise = sigma * np.random.randn(tlen)
    for i in range(tlen - 1):
        x[i + 1] = x[i] + prop(x[i], p0[i]) * dt + np.sqrt(dt) * noise[i]
        
    #Clip to reasonable level
    end_idx = int(np.where(x < 0)[0][0] - 2*365) #One half window size
        
    sin_component = get_sin(tlen, sin_model)
    #Add in a seasonal component
    x = x + sin_component
    
    #Get a version without seasonality
    x_perf = np.zeros(tlen)
    x_perf[0] = x0
    for i in range(tlen - 1):
        x_perf[i + 1] = x_perf[i] + prop(x_perf[i], p0[i]) * dt
    x_perf = x_perf + sin_component
    
    x = x / 2.5 #Modified to bring the data into quasi-NDVI space
    x_perf = x_perf / 2.5
    
    good = pd.Series(x[:end_idx], index=dt_index[:end_idx])
    s_half = pd.Series(x[end_idx:], index=dt_index[end_idx:])
    perf = pd.Series(x_perf[:end_idx], index=dt_index[:end_idx])
    return good, s_half, perf

def get_sin(tlen, sin_model):
    if sin_model == 'simple':
        return 0.5*np.sin(2*np.pi*np.arange(0,tlen,1)/365.25)
    
    elif sin_model == 'multiple':
        return 0.5*np.sin(2*np.pi*np.arange(0,tlen,1)/365.25) + 0.4*np.sin(2*np.pi*np.arange(0,tlen,1)/(365.25/2))
    
    elif sin_model == 'varying_amp':
        base_sin = 0.5*np.sin(2*np.pi*np.arange(0,tlen,1)/365.25)
        #Add randomly sized extra sin curve to each year
        extra_sin = np.zeros(tlen)
        for i in range(int(tlen/365.25)):
            i_0 = i*int(365.25)
            i_1 = (i+1) * int(365.25)
            if i_1 > tlen-1:
                i_1 = tlen
            extra_sin[i_0:i_1] = base_sin[i_0:i_1] + base_sin[i_0:i_1] * (np.random.randint(-5,5,1) / 50) #20
        return extra_sin
            
    elif sin_model == 'varying_timing':
        t = np.arange(0,tlen,1)/365.25
        base_sin = 0.5*np.sin(2*np.pi*t)
        shifted_sin = 0.5*np.sin(2*np.pi*t - np.pi/4)
        extra_sin = np.zeros(tlen)
        for i in range(int(tlen/365.25)):
            i_0 = i*int(365.25)
            i_1 = (i+1) * int(365.25)
            if i_1 > tlen-1:
                i_1 = tlen
            #phase_shift = np.random.randint(-1,1,1)
            #extra_sin[i_0:i_1] = 0.5*np.sin(2*np.pi*np.arange(0,tlen,1)/365.25 + phase_shift)[:365]
            extra_sin[i_0:i_1] = base_sin[i_0:i_1] + shifted_sin[i_0:i_1] * (np.random.randint(-5,5,1) / 50) #20
        return extra_sin
    
    elif sin_model == 'varying_amp_timing':
        t = np.arange(0,tlen,1)/365.25
        base_sin = 0.5*np.sin(2*np.pi*t)
        shifted_sin = 0.5*np.sin(2*np.pi*t - np.pi/4)
        extra_sin = np.zeros(tlen)
        for i in range(int(tlen/365.25)):
            i_0 = i*int(365.25)
            i_1 = (i+1) * int(365.25)
            if i_1 > tlen-1:
                i_1 = tlen
            extra_sin[i_0:i_1] = base_sin[i_0:i_1] + shifted_sin[i_0:i_1] * (np.random.randint(-5,5,1) / 50) + base_sin[i_0:i_1] * (np.random.randint(-5,5,1) / 50) #20
        return extra_sin
       
    elif sin_model == 'extra_noise':
        t = np.arange(0,tlen,1)/365.25
        base_sin = 0.5*np.sin(2*np.pi*t)
        extra_sin = np.zeros(tlen)
        increase = range(0,30)
        for i in range(int(tlen/365.25)):
            i_0 = i*int(365.25)
            i_1 = (i+1) * int(365.25)
            if i_1 > tlen-1:
                i_1 = tlen
            extra_sin[i_0:i_1] = base_sin[i_0:i_1] + np.random.randn(base_sin[i_0:i_1].shape[0])*(np.random.randint(-5,5,1) / 20)
        return extra_sin

ds, de = pd.Timestamp('1991-06-01'), pd.Timestamp('2022-01-01')
dt_index = pd.date_range(ds, de-pd.Timedelta(days=1),freq='d')

np.random.seed(5000)
tlen = len(dt_index)
delta_t = 0.01
x0 = 0
sigma = 0.2
prange = np.linspace(-5, 1, tlen) #Modified for later tipping
#prange = np.linspace(-5, 5, tlen) #Original model

full_signal, s_half, perf = nlm(tlen, delta_t, dt_index, x0, prange, sigma, sin_model='simple')
ser = pd.concat([full_signal, s_half])
ser = ser.resample('SMS').mean()[36:] #Drop 18 months as 'spin up'
good_data = full_signal.resample('SMS').mean()[36:] #Drop 18 months as 'spin up'
perf_ds = full_signal - perf
perf_ds = perf_ds.resample('SMS').mean()[36:]
perf = perf.resample('SMS').mean()[36:]

In [ ]:
def calc_ar1(x):
    return ma.corrcoef(ma.masked_invalid(x[:-1]), ma.masked_invalid(x[1:]))[0,1]

def fit_line2(x, y):
    import statsmodels.api as sm
    x = np.array(x).astype(float)
    X = sm.add_constant(x, prepend=True) #Add a column of ones to allow the calculation of the intercept
    model = sm.OLS(y, X, missing='drop').fit()
    intercept, slope = model.params
    pval = model.pvalues[1]

    return slope, pval, intercept

def detrend_flat(ser):
    x, y = ser.index, ser.values
    x = [(x - pd.Timestamp('1970-01-01')).days for x in x]
    m, p, b = fit_line2(x,y)
    y_ = m*np.array(x) + b
    y_fix = y - y_
    return y_fix

def daily_anomalies(ser):
    s = ser.groupby([ser.index.dayofyear], group_keys=False).apply(lambda x: x - x.mean())
    return s.sort_index()

def rolling_mean(ser, ws=120, min_per=None):
    if min_per:
        min_periods = min_per
    else:
        min_periods = ws-1
    return ser - ser.rolling(ws, center=True, min_periods=min_periods).apply(np.nanmean)

def harmonic_fit(ser, order=3):
    import statsmodels.api as sm
    harm_freq = list(range(1, order+1))
    
    x, y = ser.index, ser.values
    x = np.array([(x - pd.Timestamp('1970-01-01')).days for x in x]) / 365.25
    x_rad = x * 2 * np.pi #Convert days to radians for harmonic fitting
    
    #Create empty array to hold the independents
    nr_indep = order*2 + 2
    indep = np.empty((y.shape[0], nr_indep))
    
    #Add constant for intercept and then time
    indep[:,0] = 1
    indep[:,1] = x_rad
    
    #Now create the harmonic variables
    i = 2
    for freq in harm_freq:
        cos = np.cos(x_rad * freq)
        sin = np.sin(x_rad * freq)
        indep[:,i] = cos
        i = i + 1
        indep[:,i] = sin
        i = i + 1
        
    model = sm.OLS(y, indep, missing='drop').fit()
    coefs = model.params
    #print(coefs)
    fitted = []
    for t in range(x_rad.shape[0]):
        data = indep[t,:]
        harm_term = np.nansum(coefs*data)
        fitted.append(harm_term)
    fitted = np.array(fitted)
    return pd.Series(ser.values - fitted, index=ser.index)

In [ ]:
#Now compare 1000 iterations
def robust_stl(ser, period, stl_settings='standard'):
    
    #Standard Settings
    seasonal_jump=1
    trend_jump=1 
    low_pass_jump=1
        
    if stl_settings == 'standard':
        #Can modify smoothing window as well as fitting degrees if curious
        smooth_length=7 
        seasonal_deg=1 
        trend_deg=1
        low_pass_deg=1
        
    from statsmodels.tsa.seasonal import STL
    def nt_calc(f,ns):
        '''Calcualte the length of the trend smoother based on
        Cleveland et al., 1990'''
        nt = (1.5*f)/(1-1.5*(1/ns)) + 1 #Force fractions to be rounded up
        if int(nt) % 2. == 1:
            return int(nt)
        elif int(nt) % 2. == 0:
            return int(nt) + 1
            
    def nl_calc(f):
        '''Calcualte the length of the low-pass filter based on
        Cleveland et al., 1990'''
        if int(f) % 2. == 1:
            return int(f) + 2
        elif int(f) % 2. == 0:
            return int(f) + 1
        
    res = STL(ser, period, seasonal=smooth_length, trend=nt_calc(period,smooth_length), low_pass=nl_calc(period), robust=True,\
              seasonal_deg=seasonal_deg, trend_deg=trend_deg, low_pass_deg=low_pass_deg, seasonal_jump=seasonal_jump,\
              trend_jump=trend_jump, low_pass_jump=low_pass_jump)#, ni, no)
    return res.fit()

def get_dist(i, yrs, sin_model, sigma, stl_settings):
    ds, de = pd.Timestamp('1991-06-01'), pd.Timestamp('2022-01-01')
    dt_index = pd.date_range(ds, de-pd.Timedelta(days=1),freq='d')
    tlen = len(dt_index)
    delta_t = 0.01
    x0 = 0
    prange = np.linspace(-5, 1, tlen) #Modified for later tipping
    #prange = np.linspace(-5, 5, tlen) #Original model
    
    np.random.seed(i)
    full_signal, s_half, perf = nlm(tlen, delta_t, dt_index, x0, prange, sigma, sin_model)
    good_data = full_signal.resample('SMS',label='right').mean()[36:] #Drop 36 months as 'spin up'
    perf_ds = full_signal - perf
    perf_ds = perf_ds.resample('SMS',label='right').mean()[36:]

    rm_offline = rolling_mean(good_data, yrs*24, min_per=1)

    anom = daily_anomalies(good_data)

    deseason_rolling = harmonic_fit(rm_offline)
    anom_detrend = pd.Series(detrend_flat(anom), index=anom.index)
    
    stl = robust_stl(good_data, period=24, stl_settings=stl_settings)
    resid = stl.resid

    t = 24*yrs #SMS means 24 measurements per year

    c1 = deseason_rolling.rolling(t, min_periods=23*yrs, center=True).apply(calc_ar1)
    c3 = resid.rolling(t, min_periods=23*yrs, center=True).apply(calc_ar1)
    c4 = anom_detrend.rolling(t, min_periods=23*yrs, center=True).apply(calc_ar1)
    c6 = perf_ds.rolling(t, min_periods=23*yrs, center=True).apply(calc_ar1)
    
    return c1, c3, c4, c6

def run_samples(yrs=5, n=10, sin_model='simple', sigma=0.2, stl_settings='standard'):
    output = 'ds_n=' + str(n) + '_y=' + str(yrs) + '_sigma=' + str(sigma) + '_sinmodel=' + sin_model + '_stl=' + stl_settings + '_nr='
    if n < 50: #Kill test matrices, but make sure to leave the long calculations
        for i in range(0,6):
            try:
                os.remove(output + str(i+1) + '.npy')
            except:
                pass
    if not os.path.exists(output + '1.npy'):
        c1 = np.empty(1000)
        o1, o3, o4, o6 = np.empty((c1.shape[0], n)), np.empty((c1.shape[0], n)),\
                                 np.empty((c1.shape[0], n)), np.empty((c1.shape[0], n))
        for i in range(n):
            c1, c3, c4, c6 = get_dist(i, yrs, sin_model, sigma, stl_settings)
            s = c1.shape[0]
            o1[:s,i] = c1
            o3[:s,i] = c3
            o4[:s,i] = c4
            o6[:s,i] = c6
       
        np.save(output + '1.npy', o1)
        np.save(output + '3.npy', o3)
        np.save(output + '4.npy', o4)
        np.save(output + '5.npy', o6)

    else:
        o1 = np.load(output + '1.npy')
        o3 = np.load(output + '3.npy')
        o4 = np.load(output + '4.npy')
        o6 = np.load(output + '6.npy')
    
    return o1, o3, o4, o6

In [ ]:
#Figure 1 - Synthetic Data Deseasoning Methods
def Figure_1(axlist, yrs, sin_model, sigma, stl_settings, n=1000, axlab=True):
    ds, de = pd.Timestamp('1991-06-01'), pd.Timestamp('2022-01-01')
    dt_index = pd.date_range(ds, de-pd.Timedelta(days=1),freq='d')

    np.random.seed(5000)
    tlen = len(dt_index)
    delta_t = 0.01
    x0 = 0
    prange = np.linspace(-5, 1, tlen) #Modified for later tipping
    #prange = np.linspace(-5, 5, tlen) #Original model

    full_signal, s_half, perf = nlm(tlen, delta_t, dt_index, x0, prange, sigma, sin_model=sin_model)
    ser = pd.concat([full_signal, s_half])
    ser = ser.resample('SMS',label='right').mean()[36:] #Drop 36 months as 'spin up'
    good_data = full_signal.resample('SMS',label='right').mean()[36:] #Drop 36 months as 'spin up'
    perf_ds = full_signal - perf
    perf_ds = perf_ds.resample('SMS',label='right').mean()[36:]
    perf = perf.resample('SMS',label='right').mean()[36:]
    
    ax, ax2, ax3, ax4 = axlist

    sig_lab = 'Synthetic Time Series (sigma=' + str(sigma) + ')'
    ax.plot(good_data.index, good_data.values, 'k', label=sig_lab, linewidth=1.5)
    ax.plot(perf.index, perf.values, 'b-', label='Noiseless Synthetic Time Series', linewidth=1, alpha=0.8)
    ax.plot(ser.index[good_data.shape[0]:], ser.values[good_data.shape[0]:], 'k--', linewidth=1.5)
    ax.set_ylim(-0.1,1.1)
    ax.plot((good_data.index.max(),good_data.index.max()), ax.get_ylim(), 'k-')
    ax.legend(loc=3, fontsize=8)

    ax2.plot(perf_ds.index, perf_ds.values, 'b', label='Perfect Deseasoning')
    ax2.set_ylim(-0.07, 0.07)
    ax2.plot((good_data.index.max(),good_data.index.max()), ax2.get_ylim(), 'k-')    
    
    #Put a grey box to make clear where rolling deseasoners are less reliable
    trim_len = 12*yrs #This is one half the 5-year rolling mean window (needs to be removed for harmonic and STL)
    
    ax3.fill_betweenx((-0.09,0.09),good_data.index[0],good_data.index[trim_len], color='grey', alpha=0.25)
    ax3.fill_betweenx((-0.09,0.09),good_data.index[-trim_len],s_half.index.min(), color='grey', alpha=0.25)
    
    anom = daily_anomalies(good_data)
    anom_detrend = pd.Series(detrend_flat(anom), index=anom.index)
    ax3.plot(anom_detrend, 'k', label ='Long-term Daily Mean Removed, Linear Detrend')
            
    rm_offline = rolling_mean(good_data, yrs*24, min_per=1)
    deseason_rolling = harmonic_fit(rm_offline)
    ax3.plot(deseason_rolling.index, deseason_rolling.values, 'r', alpha=0.5)

    deseason_rolling.values[:trim_len] = np.nan #Manually kill values that are less reliable
    deseason_rolling.values[-trim_len:] = np.nan
    ax3.plot(deseason_rolling.index, deseason_rolling.values, 'r', label='Rolling Mean Detrend, Harmonic Deseason')
    
    stl = robust_stl(good_data, period=24, stl_settings=stl_settings)
    resid = stl.resid
    ax3.plot(resid.index, resid.values, 'm', alpha=0.5)
    resid.values[:trim_len] = np.nan #Manually kill values that are less reliable
    resid.values[-trim_len:] = np.nan
    ax3.plot(resid.index, resid.values, 'm', label ='STL Deseasoning/Detrending')
    
    ax3.set_ylim(-0.09,0.09)
    ax3.plot((good_data.index.max(),good_data.index.max()), ax3.get_ylim(), 'k-')
    
    o1, o3, o4, o6 = run_samples(yrs=yrs, n=n, sin_model=sin_model, sigma=sigma, stl_settings=stl_settings)
    
    labs = ['Perfect Deseason/Detrend','Rolling Mean Detrend\nHarmonic Deseason','Long-term Daily Mean\nRemoved, Linear Detrend','STL Deseasoning/Detrending']
    colors = ['b','r','k','m']
    for i, o in enumerate([o6, o1, o4, o3]):
        oo = o.copy()
        oo[o < 0] = np.nan
        oo[o > 1] = np.nan

        #Trim off data because not all time series transition at the same time!
        trans_stop = np.argwhere(good_data.index >= s_half.index.min())[0][0] - int(2.5*24)
        
        x = good_data.index[:trans_stop]#-60]
        y = np.nanmean(oo,1)[:trans_stop]#-60]
        y_std = np.nanstd(oo,1)[:trans_stop]#-60]

        full_trim = 24*yrs #Since two 5-year windows, rolling ac1 should drop full 5 years from original data len
        
        if i in [0, 2]:
            ax4.fill_between(x, y - y_std, y + y_std, color=colors[i], alpha=0.1)
            ax4.plot(x,y, label=labs[i], color=colors[i])
            
        elif i in [1, 3]:
            #Trim case
            min_date = deseason_rolling.index[full_trim]#pd.Timestamp('1995-06-01')
            max_date = deseason_rolling.index[-full_trim]#pd.Timestamp('2015-05-01')
            m, ma = np.argwhere(x == min_date)[0][0], np.argwhere(x == max_date)[0][0]
            #print(m, ma)
            x_ = x[m:ma]
            y_ = y[m:ma]
            y_std_ = y_std[m:ma]
            ax4.fill_between(x_, y_ - y_std_, y_ + y_std_, color=colors[i], alpha=0.1)
            ax4.plot(x_, y_, label=labs[i], color=colors[i])
            
            ax4.plot(x[:m], y[:m], color=colors[i], linestyle='--')
            ax4.plot(x[ma:], y[ma:], color=colors[i], linestyle='--')
            
    ax3.legend(loc=8, fontsize=7)#, loc=8)#8)
    ax4.legend(loc=4, fontsize=6)#8)
    if axlab:
        ax.set_ylabel('Synthetic Data', fontsize=12, fontweight='bold')
        ax2.set_ylabel('Perfect Deseasoning\nand Detrending', fontsize=12, fontweight='bold')
        ax3.set_ylabel('Deseasoned and\nDetrended Data', fontsize=12, fontweight='bold')
        ax4.set_ylabel('Avg. Rolling\nAutocorrelation (n=' + str(n) + ')', fontsize=12, fontweight='bold')
    ax4.set_xlabel('Time', fontsize=12, fontweight='bold')
    for a in [ax, ax2, ax3, ax4]:
        a.set_xlim(pd.Timestamp('1992-06-01'), pd.Timestamp('2021-06-01'))

    for a in [ax2, ax3]:
        a.plot(a.get_xlim(), (0,0), 'k--')
    ax4.set_ylim(0.2,0.9)


In [ ]:
#FOR QUICK TESTS, RUN N=10. Otherwise it's SLOW
yrs = 5
sigma = 0.2
n = 10#00
stl_settings = 'standard'

gs = gridspec.GridSpec(4,2) 
gs.update(hspace=0.25,wspace=0.25)
f = plt.figure(figsize=(16,10))

ax = f.add_subplot(gs[0,0])
ax2 = f.add_subplot(gs[1,0])
ax3 = f.add_subplot(gs[2,0])
ax4 = f.add_subplot(gs[3,0])
ax5 = f.add_subplot(gs[0,1])  
ax6 = f.add_subplot(gs[1,1])  
ax7 = f.add_subplot(gs[2,1])  
ax8 = f.add_subplot(gs[3,1])  

Figure_1((ax, ax2, ax3, ax4), yrs, 'simple', sigma, stl_settings, n=n)
Figure_1((ax5, ax6, ax7, ax8), yrs, 'varying_amp_timing', sigma, stl_settings, n=n, axlab=False)

ax.text(0, 1, '(A)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax.transAxes)
ax2.text(0, 1, '(C)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax2.transAxes)
ax3.text(0, 1, '(E)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax3.transAxes)
ax4.text(0, 1, '(G)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax4.transAxes)

ax5.text(0, 1, '(B)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax5.transAxes)
ax6.text(0, 1, '(D)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax6.transAxes)
ax7.text(0, 1, '(F)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax7.transAxes)
ax8.text(0, 1, '(H)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax8.transAxes)

ax.set_title('Simple Sinusoidal Model', fontweight='bold', fontsize=18)
ax5.set_title('Variable Sinusoidal Model', fontweight='bold', fontsize=18)

plt.tight_layout()
f.savefig('Fig01.png', dpi=300)
plt.close('all')

In [ ]:
#Figure 2 - Synthetic Data with Gaps
def create_deseason(ser):
    rm_offline = rolling_mean(ser, yrs*24, min_per=1)  
    deseason_rolling = harmonic_fit(rm_offline)
    return deseason_rolling

def forced_gap(orig_ser, sample_pct=0, gap_months=[10,11,12,1,2,3,4,5]):
    ser = orig_ser.copy()

    #Add random gaps for cloud cover according to some percentage
    if sample_pct > 0:
        if sample_pct > 1:
            sample_pct = sample_pct / 100. #Can take percentage in either decimal or as parts of 100
        else:
            pass #sample_pct needs to be a percentage (e.g., 0.2)
        size = ser.shape[0]
        idx = np.random.choice(size, size=int(size*sample_pct), replace=False)
        ser[idx] = np.nan
        
    if gap_months:
        output = []
        #Choose random months to cover with snow or clouds, based on 'water year' of [Oct-Oct], defined by 'gap_months'
        for yr in np.unique(ser.index.year):
            #Split into water years
            idx_start = np.logical_and(ser.index.year == yr, ser.index.month >= 10)
            amin = ser.index[idx_start].min()
            idx_end = np.logical_and(ser.index.year == yr + 1, ser.index.month < 10)
            amax = ser.index[idx_end].max()
            wy = ser[amin:amax]
            
            for mo in gap_months:
                if mo < 10: #If we are at the next year already for winter gaps
                    idx = np.logical_and(wy.index.year == yr + 1, wy.index.month == mo)
                    wy[idx] = np.nan
                else:
                    idx = np.logical_and(wy.index.year == yr, wy.index.month == mo)
                    wy[idx] = np.nan
            output.append(wy)
            
        ser = pd.concat(output)
        ser = ser[ser.index.year > np.nanmin(ser.index.year)] #Drop first incomplete year
        orig_ser = orig_ser[orig_ser.index.year > np.nanmin(orig_ser.index.year)]

    return orig_ser, ser

def sample_gaps(n=100, sample_pct=0, gap_months=None, resample=True):
    def get_ac1(i, sample_pct=0, gap_months=None, resample=True):
        ds, de = pd.Timestamp('1991-06-01'), pd.Timestamp('2022-01-01')
        dt_index = pd.date_range(ds, de-pd.Timedelta(days=1),freq='d')
        tlen = len(dt_index)
        delta_t = 0.01
        x0 = 0
        sigma = 0.2
        prange = np.linspace(-5, 1, tlen) #Modified for later tipping
        #prange = np.linspace(-5, 5, tlen) #Original model

        np.random.seed(i)
        full_signal, s_half, perf = nlm(tlen, delta_t, dt_index, x0, prange, sigma, sin_model='simple')
        good_data = full_signal
        if resample:
            good_data = good_data.resample('SMS').mean()[36:] #Drop 36 months as 'spin up'
        else:
            good_data = good_data[36:]

        _, gap_signal = forced_gap(full_signal, sample_pct=sample_pct, gap_months=gap_months)
        if resample:
            gap_signal = gap_signal.resample('SMS').mean()[36:]
        else:
            gap_signal = gap_signal[36:]

        full_ds = create_deseason(good_data)
        gap_ds = create_deseason(gap_signal)

        c1 = calc_ar1(full_ds)
        c2 = calc_ar1(gap_ds)

        return c1, c2

    o1, o2 = np.empty(n), np.empty(n)
    o1.fill(np.nan)
    o2.fill(np.nan)
    for i in range(n):
        c1, c2 = get_ac1(i, sample_pct=sample_pct, gap_months=gap_months,resample=resample)
        o1[i] = c1
        o2[i] = c2
    return o1, o2

In [ ]:
#Supplemental Figure -- Gap Length
raw, gap = sample_gaps(n=100, sample_pct=50, gap_months=None, resample=True)
raw2, gap2 = sample_gaps(n=100, sample_pct=50, gap_months=[1,2,3], resample=True)
raw3, gap3 = sample_gaps(n=100, sample_pct=50, gap_months=[1,2,3,4,5,6], resample=True)
raw4, gap4 = sample_gaps(n=100, sample_pct=50, gap_months=[1,2,3,4,5,6,7,8,9], resample=True)

ls = np.linspace(raw.min(), raw.max(), 100)

f, ((ax, ax2), (ax3, ax4)) = plt.subplots(2,2, figsize=(10,10))
ax.plot(raw, gap, 'b.', label='Only Random Gaps, n=100')
slp, inter, _, _ = theilslopes(gap, raw, alpha=0.95)
ax.plot(ls, slp*ls + inter, 'k--')
ax.plot(ls, slp*ls + inter, 'k--', label='Slope = %.3g' % slp)

ls = np.linspace(raw2.min(), raw2.max(), 100)
ax2.plot(raw2, gap2, 'b.', label='Random Gaps + 3-month Gaps, n=100')
slp, inter, _, _ = theilslopes(gap2, raw2, alpha=0.95)
ax2.plot(ls, slp*ls + inter, 'k--')
ax2.plot(ls, slp*ls + inter, 'k--', label='Slope = %.3g' % slp)

ls = np.linspace(raw3.min(), raw3.max(), 100)
ax3.plot(raw3, gap3, 'b.', label='Random Gaps + 6-month Gaps, n=100')
slp, inter, _, _ = theilslopes(gap3, raw3, alpha=0.95)
ax3.plot(ls, slp*ls + inter, 'k--', label='Slope = %.3g' % slp)

ls = np.linspace(raw4.min(), raw4.max(), 100)
ax4.plot(raw4, gap4, 'b.', label='Random Gaps + 9-month Gaps, n=100')
slp, inter, _, _ = theilslopes(gap4, raw4, alpha=0.95)
ax4.plot(ls, slp*ls + inter, 'k--', label='Slope = %.3g' % slp)

plt.tight_layout()
ax.text(0, 1, '(A)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax.transAxes)
ax2.text(0, 1, '(B)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax2.transAxes)
ax3.text(0, 1, '(C)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax3.transAxes)
ax4.text(0, 1, '(D)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax4.transAxes)
for a in [ax, ax2, ax3, ax4]:
    a.set_xlabel('Lag1-Autocorrelation (Gap-Free)', fontsize=14, fontweight='bold')    
    a.set_ylabel('Lag1-Autocorrelation (Gappy)', fontsize=14, fontweight='bold')
    a.set_xlim(0.3, 1)
    a.set_ylim(0.3, 1)
    a.legend(loc=4, fontsize=10)

for a in [ax, ax2]:
    a.set_xlabel('')
for a in [ax2, ax4]:
    a.set_ylabel('')
    
f.savefig('SFig01_GapLength.png', dpi=300, bbox_inches='tight')

In [ ]:
#Supplemental Figure -- Example Gappy Time Series
np.random.seed(5000)
_, winter_gap_signal = forced_gap(full_signal, sample_pct=50, gap_months=None)
_, summer_gap_signal = forced_gap(full_signal, sample_pct=50, gap_months=[1,2,3])
_, cloud_gap_signal = forced_gap(full_signal, sample_pct=50, gap_months=[1,2,3,4,5,6])

winter = winter_gap_signal.resample('SMS').mean()[36:]
summer = summer_gap_signal.resample('SMS').mean()[36:]
cloud = cloud_gap_signal.resample('SMS').mean()[36:]

full_ds = create_deseason(good_data)
winter_ds = create_deseason(winter)
summer_ds = create_deseason(summer)
cloud_ds = create_deseason(cloud)

f, (ax, ax2, ax3, ax4) = plt.subplots(4, figsize=(10,10))
ax.plot(good_data, 'b', label='Raw Data')
axa = ax.twinx()
axa.plot(full_ds, 'r', label='Residual')
ac = '%.3g' % calc_ar1(full_ds)
ax.set_title('No Gap AC1: ' + ac)

ax2.plot(winter, 'b', label='Raw Data')
ax2a = ax2.twinx()
ax2a.plot(winter_ds, 'r', label='Residual')
ac = '%.3g' % calc_ar1(winter_ds)
ax2.set_title('Random Cloud Gaps AC1: ' + ac)

ax3a = ax3.twinx()
ax3.plot(summer, 'b', label='Raw Data')
ax3a.plot(summer_ds, 'r', label='Residual')
ac = '%.3g' % calc_ar1(summer_ds)
ax3.set_title('Random Cloud Gaps + 3-month Gap AC1: ' + ac)

ax4a = ax4.twinx()
ax4.plot(cloud, 'b', label='Raw Data')
ax4a.plot(cloud_ds, 'r', label='Residual')
ac = '%.3g' % calc_ar1(cloud_ds)
ax4.set_title('Random Cloud Gaps + 6-month Gap AC1: ' + ac)

for a in [ax, ax2, ax3, ax4]:
    a.set_ylabel('Raw Data', fontsize=12, fontweight='bold')
    a.yaxis.label.set_color('b')
    a.tick_params(axis='y', colors='b')

for a in [axa, ax2a, ax3a, ax4a]:
    a.set_ylabel('Residual', fontsize=12, fontweight='bold')
    a.yaxis.label.set_color('r')
    a.tick_params(axis='y', colors='r')

ax4.set_xlabel('Time', fontsize=12, fontweight='bold')

ax.text(0, 1, '(A)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax.transAxes)
ax2.text(0, 1, '(B)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax2.transAxes)
ax3.text(0, 1, '(C)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax3.transAxes)
ax4.text(0, 1, '(D)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax4.transAxes)

plt.tight_layout()
f.savefig('SFig02_GapTS.png', dpi=300)

In [ ]:
#Supplemental Figure -- Resampling over Gaps
rawa, gapa = sample_gaps(n=100, sample_pct=50, gap_months=None, resample=True)
raw2a, gap2a = sample_gaps(n=100, sample_pct=50, gap_months=None, resample=False)

f, (ax, ax2) = plt.subplots(1,2, figsize=(10, 5))
ls = np.linspace(rawa.min(), rawa.max(), 100)
ax.plot(rawa, gapa, 'b.', label='Random Gaps, bi-weekly resampled, n=100')
slp, inter, _, _ = theilslopes(gapa, rawa, alpha=0.95)
ax.plot(ls, slp*ls + inter, 'k--')
ax.plot(ls, slp*ls + inter, 'k--', label='Slope = %.3g' % slp)

ls = np.linspace(raw2a.min(), raw2a.max(), 100)
ax2.plot(raw2a, gap2a, 'b.', label='Random Gaps, no resampling, n=100')
slp, inter, _, _ = theilslopes(gap2a, raw2a, alpha=0.95)
ax2.plot(ls, slp*ls + inter, 'k--')
ax2.plot(ls, slp*ls + inter, 'k--', label='Slope = %.3g' % slp)

for a in [ax, ax2]:
    a.set_xlabel('Lag1-Autocorrelation (Gap-Free)', fontsize=14, fontweight='bold')    
    a.set_ylabel('Lag1-Autocorrelation (Gappy)', fontsize=14, fontweight='bold')
    a.set_xlim(0.3, 1)
    a.set_ylim(0.3, 1)
    a.legend(loc=4, fontsize=10)
    
ax2.set_xlim(0.9, 1)
ax2.set_ylim(0.9, 1)

ax.text(0, 1, '(A)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax.transAxes)
ax2.text(0, 1, '(B)', fontsize=16, fontweight='bold', va='top', ha='left', transform=ax2.transAxes)
ax2.set_ylabel('')
plt.tight_layout()
f.savefig('SFig03_ResampGaps.png', dpi=300)